<h1 align=center><font size = 5>Segmenting and Clustering Neighborhoods in Toronto</font></h1>

## Introduction

This part of the project scrapes data from a wikipedia page containing postal codes in Toronto, CA.  It places the data in a pandas dataframe. 

As a first order of business, I will download various needed libraries.  This notebook was developed locally using Anaconda 3 with a virtual environment containing the needed libraries.  If they are not present (conda-forge geopy, folium) then uncomment the #!conda install lines.  Some of these libraries are not used in the first part of the project, but are loaded now by convention.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


## 1. Download Dataset

Here, the BeautifulSoup library is downloaded:

In [2]:
from urllib.request import urlopen
from bs4 import BeautifulSoup
import lxml
import html5lib

This is the target webpage:

In [3]:
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
html = urlopen(url)
soup = BeautifulSoup(html, 'html.parser')
type(soup)


bs4.BeautifulSoup

This code extracts the HTML table element from the page and stores it as My_table

In [4]:
My_table = soup.find('table',{'class':'wikitable sortable'})

Create a new Pandas DataFrame for our data

In [5]:
column_names = ['PostalCode', 'Borough', 'Neighborhood']
postdf=pd.DataFrame(columns=column_names)

Ignoring the first row (containing column names) each row is read, cleaned, and, if appropriate, appended to the previously created DataFrame.

In [6]:
firstRow = True
for myrow in My_table.find_all('tr'):   # tr is HTML for Table Row
    if firstRow == False:
        lst=myrow.text.split('\n')  # Each row reads in as a blank, three data items, and another blank
        pc=lst[1]                   # PostalCode
        b=lst[2]                    # Borough
        neigh=lst[3]                # Neighborhoon
        if neigh == 'Not assigned': # Unassigned neighborhoods are assigned to the Borough name
            neigh = b
        rowdf = pd.DataFrame([[pc, b, neigh]], columns=column_names)
        if b != 'Not assigned':     # if Borough is unassigned, ignore the row
            postdf = postdf.append(rowdf, ignore_index=True)
    else:
        firstRow = False

print(f"DataFrame contains {postdf.shape[0]} rows.")

DataFrame contains 210 rows.


Written and submitted by Tom Kenny for IBM Data Science Capstone Course on Coursera

## Phase 2 - Analysing Toronto Neighborhoods

I found a nice Canadian geocoder, but after a few calls I was throttled.
Didn't seem too expensive, and it would be free for non-profits, but I was pressed for time.

In [36]:
# didn't use these
# base='https://geocoder.ca/?postal='
# last = '&geoit=xml&json=1'

Add Lati and longi columns (worry about content later)

In [34]:
tempdf = pd.DataFrame(columns=['lati', 'longi'])
postdf = pd.concat([postdf, tempdf],sort=True)
postdf.head()

Borough      Neighborhood PostalCode lati longi
0        North York         Parkwoods        M3A  209   NaN
1        North York  Victoria Village        M4A  209   NaN
2  Downtown Toronto      Harbourfront        M5A  209   NaN
3        North York  Lawrence Heights        M6A  209   NaN
4        North York    Lawrence Manor        M6A  209   NaN

Having given up on geocoder from the web, I am using the provided data file, reading it into latlongdf

In [43]:
latlongurl="https://cocl.us/Geospatial_data"
latlongdf=pd.read_csv(latlongurl)

In [44]:
latlongdf

Postal Code   Latitude  Longitude
0           M1B  43.806686 -79.194353
1           M1C  43.784535 -79.160497
2           M1E  43.763573 -79.188711
3           M1G  43.770992 -79.216917
4           M1H  43.773136 -79.239476
5           M1J  43.744734 -79.239476
6           M1K  43.727929 -79.262029
7           M1L  43.711112 -79.284577
8           M1M  43.716316 -79.239476
9           M1N  43.692657 -79.264848
10          M1P  43.757410 -79.273304
11          M1R  43.750072 -79.295849
12          M1S  43.794200 -79.262029
13          M1T  43.781638 -79.304302
14          M1V  43.815252 -79.284577
15          M1W  43.799525 -79.318389
16          M1X  43.836125 -79.205636
17          M2H  43.803762 -79.363452
18          M2J  43.778517 -79.346556
19          M2K  43.786947 -79.385975
20          M2L  43.757490 -79.374714
21          M2M  43.789053 -79.408493
22          M2N  43.770120 -79.408493
23          M2P  43.752758 -79.400049
24          M2R  43.782736 -79.442259
25          M3A  43.753259 -79.329656
26          M3B  43.745906 -79.352188
27          M3C  43.725900 -79.340923
28          M3H  43.754328 -79.442259
29          M3J  43.767980 -79.487262
30          M3K  43.737473 -79.464763
31          M3L  43.739015 -79.506944
32          M3M  43.728496 -79.495697
33          M3N  43.761631 -79.520999
34          M4A  43.725882 -79.315572
35          M4B  43.706397 -79.309937
36          M4C  43.695344 -79.318389
37          M4E  43.676357 -79.293031
38          M4G  43.709060 -79.363452
39          M4H  43.705369 -79.349372
40          M4J  43.685347 -79.338106
41          M4K  43.679557 -79.352188
42          M4L  43.668999 -79.315572
43          M4M  43.659526 -79.340923
44          M4N  43.728020 -79.388790
45          M4P  43.712751 -79.390197
46          M4R  43.715383 -79.405678
47          M4S  43.704324 -79.388790
48          M4T  43.689574 -79.383160
49          M4V  43.686412 -79.400049
50          M4W  43.679563 -79.377529
51          M4X  43.667967 -79.367675
52          M4Y  43.665860 -79.383160
53          M5A  43.654260 -79.360636
54          M5B  43.657162 -79.378937
55          M5C  43.651494 -79.375418
56          M5E  43.644771 -79.373306
57          M5G  43.657952 -79.387383
58          M5H  43.650571 -79.384568
59          M5J  43.640816 -79.381752
60          M5K  43.647177 -79.381576
61          M5L  43.648198 -79.379817
62          M5M  43.733283 -79.419750
63          M5N  43.711695 -79.416936
64          M5P  43.696948 -79.411307
65          M5R  43.672710 -79.405678
66          M5S  43.662696 -79.400049
67          M5T  43.653206 -79.400049
68          M5V  43.628947 -79.394420
69          M5W  43.646435 -79.374846
70          M5X  43.648429 -79.382280
71          M6A  43.718518 -79.464763
72          M6B  43.709577 -79.445073
73          M6C  43.693781 -79.428191
74          M6E  43.689026 -79.453512
75          M6G  43.669542 -79.422564
76          M6H  43.669005 -79.442259
77          M6J  43.647927 -79.419750
78          M6K  43.636847 -79.428191
79          M6L  43.713756 -79.490074
80          M6M  43.691116 -79.476013
81          M6N  43.673185 -79.487262
82          M6P  43.661608 -79.464763
83          M6R  43.648960 -79.456325
84          M6S  43.651571 -79.484450
85          M7A  43.662301 -79.389494
86          M7R  43.636966 -79.615819
87          M7Y  43.662744 -79.321558
88          M8V  43.605647 -79.501321
89          M8W  43.602414 -79.543484
90          M8X  43.653654 -79.506944
91          M8Y  43.636258 -79.498509
92          M8Z  43.628841 -79.520999
93          M9A  43.667856 -79.532242
94          M9B  43.650943 -79.554724
95          M9C  43.643515 -79.577201
96          M9L  43.756303 -79.565963
97          M9M  43.724766 -79.532242
98          M9N  43.706876 -79.518188
99          M9P  43.696319 -79.532242
100         M9R  43.688905 -79.554724
101         M9V  43.739416 -79.588437
102         M9W  43.706748 -79.594054

Two functions that return latitude and longitude given a postal code

In [63]:
def getlat(pc):  
    for index, row in latlongdf.iterrows():
        if row['Postal Code'] == pc:
            return row['Latitude']
    return 0.0

def getlong(pc):
    for index, row in latlongdf.iterrows():
        if row['Postal Code'] == pc:
            return row['Longitude']
    return 0.0

Iterate through postdf and fill in latitude and longitude values

In [71]:
for index, row in postdf.iterrows():
    pc=row['PostalCode']
    postdf.loc[index, 'lati'] = getlat(pc)
    postdf.loc[index, 'longi'] = getlong(pc)

postdf.head()
    

Borough      Neighborhood PostalCode       lati      longi
0        North York         Parkwoods        M3A  43.753259 -79.329656
1        North York  Victoria Village        M4A  43.725882 -79.315572
2  Downtown Toronto      Harbourfront        M5A  43.654260 -79.360636
3        North York  Lawrence Heights        M6A  43.718518 -79.464763
4        North York    Lawrence Manor        M6A  43.718518 -79.464763

Generate a map 

In [66]:
# create map of Toronto using latitude and longitude values
t_latitude = 43.654260
t_longitude = -79.360636
map_toronto = folium.Map(location=[t_latitude, t_longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(postdf['lati'], postdf['longi'], postdf['Borough'], postdf['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

In [ ]:
Set up values for calling requests to Foursquare

In [72]:
CLIENT_ID = 'F3SQKWY1C2VSBLT2OHLDAYZHCCLBOZK0PY5YTAUGRPA3VTOU' # your Foursquare ID
CLIENT_SECRET = 'T2AW5J5LTZZYVKIBE1MZ51TK1WFCLO5E2VW1XI3B3B4PZ3C4' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 

In [ ]:
This function returns venues that are near the neighborhood as defined by latitude and longitude

In [79]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [80]:
toronto_venues = getNearbyVenues(names=postdf['Neighborhood'],
                                   latitudes=postdf['lati'],
                                   longitudes=postdf['longi']
                                  )

Parkwoods
Victoria Village
Harbourfront
Lawrence Heights
Lawrence Manor
Queen's Park
Queen's Park
Rouge
Malvern
Don Mills North
Woodbine Gardens
Parkview Hill
Ryerson
Garden District
Glencairn
Cloverdale
Islington
Martin Grove
Princess Gardens
West Deane Park
Highland Creek
Rouge Hill
Port Union
Flemingdon Park
Don Mills South
Woodbine Heights
St. James Town
Humewood-Cedarvale
Bloordale Gardens
Eringate
Markland Wood
Old Burnhamthorpe
Guildwood
Morningside
West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor
Downsview North
Wilson Heights
Thorncliffe Park
Adelaide
King
Richmond
Dovercourt Village
Dufferin
Scarborough Village
Fairview
Henry Farm
Oriole
Northwood Park
York University
East Toronto
Harbourfront East
Toronto Islands
Union Station
Little Portugal
Trinity
East Birchmount Park
Ionview
Kennedy Park
Bayview Village
CFB Toronto
Downsview East
The Danforth West
Riverdale
Design Exchange
Toronto 

In [81]:
print(toronto_venues.shape)
toronto_venues.head()

(4288, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2         Parkwoods              43.753259              -79.329656   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                    Venue  Venue Latitude  Venue Longitude     Venue Category  
0         Brookbanks Park       43.751976       -79.332140               Park  
1           Variety Store       43.751974       -79.333114  Food & Drink Shop  
2           GreenWin pool       43.756232       -79.333842               Pool  
3  Victoria Village Arena       43.723481       -79.315635       Hockey Arena  
4             Tim Hortons       43.725517       -79.313103        Coffee Shop

In [82]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                               
Adelaide                                                             100   
Agincourt                                                              5   
Agincourt North                                                        2   
Albion Gardens                                                         9   
Alderwood                                                             10   
Bathurst Manor                                                        19   
Bathurst Quay                                                         14   
Bayview Village                                                        4   
Beaumond Heights                                                       9   
Bedford Park                                                          25   
Berczy Park                                                           58   
Birch Cliff                                                            4   
Bloordale Gardens                                                      7   
Brockton                                                              24   
Business Reply Mail Processing Centre 969 Eastern                     18   
CFB Toronto                                                            3   
CN Tower                                                              14   
Cabbagetown                                                           48   
Caledonia-Fairbanks                                                    4   
Canada Post Gateway Processing Centre                                 11   
Cedarbrae                                                              8   
Central Bay Street                                                    85   
Chinatown                                                             86   
Christie                                                              18   
Church and Wellesley                                                  85   
Clairlea                                                              10   
Clarks Corners                                                        13   
Cliffcrest                                                             3   
Cliffside                                                              3   
Cliffside West                                                         4   
Commerce Court                                                       100   
Davisville                                                            38   
Davisville North                                                       8   
Deer Park                                                             14   
Del Ray                                                                5   
Design Exchange                                                      100   
Don Mills North                                                        6   
Don Mills South                                                       23   
Dorset Park                                                            5   
Dovercourt Village                                                    16   
Downsview                                                              4   
Downsview Central                                                      4   
Downsview East                                                         3   
Downsview North                                                       19   
Downsview Northwest                                                    4   
Downsview West                                                         4   
Dufferin                                                              16   
East Birchmount Park                                                   5   
East Toronto                                                           3   
Emery                                                                  1   
Eringate                                                               7   
Exhibition Place       

In [83]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 266 uniques categories.


One Hot Encoding will allow us to group the neighborhoods by the presence of similar venues

In [84]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  Airport  \
0            0                  0                  0        0   
1            0                  0                  0        0   
2            0                  0                  0        0   
3            0                  0                  0        0   
4            0                  0                  0        0   

   Airport Food Court  Airport Gate  Airport Lounge  Airport Service  \
0                   0             0               0                0   
1                   0             0               0                0   
2                   0             0               0                0   
3                   0             0               0                0   
4                   0             0               0                0   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0                 0                    0             0         0            0   
1                 0                    0             0         0            0   
2                 0                    0             0         0            0   
3                 0                    0             0         0            0   
4                 0                    0             0         0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          0           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Beach  Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  \
0      0                0         0           0                   0   
1      0                0         0           0                   0   
2      0                0         0           0                   0   
3      0                0         0           0                   0   
4      0                0         0           0                   0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0          0       0              0          0         0   
1          0       0              0          0         0   
2          0       0              0          0         0   
3          0       0              0          0         0   
4          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   


In [85]:
toronto_onehot.shape

(4288, 266)

In [86]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                             Adelaide     0.000000   
1                                            Agincourt     0.000000   
2                                      Agincourt North     0.000000   
3                                       Albion Gardens     0.000000   
4                                            Alderwood     0.000000   
5                                       Bathurst Manor     0.000000   
6                                        Bathurst Quay     0.000000   
7                                      Bayview Village     0.000000   
8                                     Beaumond Heights     0.000000   
9                                         Bedford Park     0.000000   
10                                         Berczy Park     0.000000   
11                                         Birch Cliff     0.000000   
12                                   Bloordale Gardens     0.000000   
13                                            Brockton     0.000000   
14   Business Reply Mail Processing Centre 969 Eastern     0.055556   
15                                         CFB Toronto     0.000000   
16                                            CN Tower     0.000000   
17                                         Cabbagetown     0.000000   
18                                 Caledonia-Fairbanks     0.000000   
19               Canada Post Gateway Processing Centre     0.000000   
20                                           Cedarbrae     0.000000   
21                                  Central Bay Street     0.011765   
22                                           Chinatown     0.000000   
23                                            Christie     0.000000   
24                                Church and Wellesley     0.011765   
25                                            Clairlea     0.000000   
26                                      Clarks Corners     0.000000   
27                                          Cliffcrest     0.000000   
28                                           Cliffside     0.000000   
29                                      Cliffside West     0.000000   
30                                      Commerce Court     0.000000   
31                                          Davisville     0.000000   
32                                    Davisville North     0.000000   
33                                           Deer Park     0.000000   
34                                             Del Ray     0.000000   
35                                     Design Exchange     0.000000   
36                                     Don Mills North     0.000000   
37                                     Don Mills South     0.000000   
38                                         Dorset Park     0.000000   
39                                  Dovercourt Village     0.000000   
40                                           Downsview     0.000000   
41                                   Downsview Central     0.000000   
42                                      Downsview East     0.000000   
43                                     Downsview North     0.000000   
44                                 Downsview Northwest     0.000000   
45                                      Downsview West     0.000000   
46                                            Dufferin     0.000000   
47                                East Birchmount Park     0.000000   
48                                        East Toronto     0.000000   
49                                               Emery     0.000000   
50                                            Eringate     0.000000   
51                                    Exhibition Place     0.000000   
52                                            Fairview     0.000000   
53                                First Canadian Place     0.000000   
54                                     Flemingdon Park     0.000000   
55                                   Forest Hill North     0.00000

In [87]:
toronto_grouped.shape

(199, 266)

In [ ]:
For fun, generate a list of the top venues by neighborhood

In [88]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide----
         venue  freq
0  Coffee Shop  0.07
1         Café  0.04
2   Steakhouse  0.04
3          Bar  0.04
4   Restaurant  0.03


----Agincourt----
                       venue  freq
0                     Lounge   0.2
1  Latin American Restaurant   0.2
2               Skating Rink   0.2
3             Breakfast Spot   0.2
4             Clothing Store   0.2


----Agincourt North----
               venue  freq
0         Playground   0.5
1               Park   0.5
2        Yoga Studio   0.0
3        Men's Store   0.0
4  Mobile Phone Shop   0.0


----Albion Gardens----
                  venue  freq
0         Grocery Store  0.22
1              Pharmacy  0.11
2  Fast Food Restaurant  0.11
3            Beer Store  0.11
4        Sandwich Place  0.11


----Alderwood----
                venue  freq
0         Pizza Place   0.2
1  Athletics & Sports   0.1
2        Dance Studio   0.1
3            Pharmacy   0.1
4         Coffee Shop   0.1


----Bathurst Manor----
                venue

         venue  freq
0         Park  0.33
1      Airport  0.33
2  Snack Place  0.33
3  Yoga Studio  0.00
4  Men's Store  0.00


----Downsview North----
                venue  freq
0         Coffee Shop  0.11
1         Pizza Place  0.05
2  Frozen Yogurt Shop  0.05
3         Supermarket  0.05
4                Bank  0.05


----Downsview Northwest----
                  venue  freq
0  Gym / Fitness Center  0.25
1         Grocery Store  0.25
2    Athletics & Sports  0.25
3          Liquor Store  0.25
4  Other Great Outdoors  0.00


----Downsview West----
           venue  freq
0  Grocery Store  0.25
1           Park  0.25
2           Bank  0.25
3          Hotel  0.25
4    Yoga Studio  0.00


----Dufferin----
                       venue  freq
0                   Pharmacy  0.12
1                     Bakery  0.12
2  Middle Eastern Restaurant  0.06
3                       Bank  0.06
4                    Brewery  0.06


----East Birchmount Park----
                       venue  freq
0           

4        Yoga Studio  0.00


----Kingsway Park South East----
                        venue  freq
0              Baseball Field   1.0
1                 Yoga Studio   0.0
2               Metro Station   0.0
3  Modern European Restaurant   0.0
4           Mobile Phone Shop   0.0


----Kingsway Park South West----
                  venue  freq
0                   Gym  0.07
1         Tanning Salon  0.07
2         Grocery Store  0.07
3           Flower Shop  0.07
4  Fast Food Restaurant  0.07


----L'Amoreaux East----
               venue  freq
0         Playground   0.5
1               Park   0.5
2        Yoga Studio   0.0
3        Men's Store   0.0
4  Mobile Phone Shop   0.0


----L'Amoreaux West----
                  venue  freq
0  Fast Food Restaurant  0.20
1    Chinese Restaurant  0.13
2       Bubble Tea Shop  0.07
3        Sandwich Place  0.07
4        Discount Store  0.07


----Lawrence Heights----
                venue  freq
0      Clothing Store  0.18
1       Women's Store  0.09
2 

                    venue  freq
0        Greek Restaurant  0.21
1             Coffee Shop  0.10
2      Italian Restaurant  0.07
3  Furniture / Home Store  0.05
4          Ice Cream Shop  0.05


----Roncesvalles----
                venue  freq
0           Gift Shop  0.15
1         Coffee Shop  0.08
2  Italian Restaurant  0.08
3             Dog Run  0.08
4          Restaurant  0.08


----Rosedale----
         venue  freq
0         Park  0.50
1   Playground  0.25
2        Trail  0.25
3  Yoga Studio  0.00
4  Men's Store  0.00


----Roselawn----
                        venue  freq
0                      Garden   1.0
1                 Yoga Studio   0.0
2               Metro Station   0.0
3  Modern European Restaurant   0.0
4           Mobile Phone Shop   0.0


----Rouge----
                             venue  freq
0             Fast Food Restaurant   1.0
1  Molecular Gastronomy Restaurant   0.0
2                     Liquor Store   0.0
3                           Lounge   0.0
4               

4   Steakhouse  0.04


----Toronto Islands----
                venue  freq
0         Coffee Shop  0.12
1            Aquarium  0.05
2               Hotel  0.04
3  Italian Restaurant  0.04
4                Café  0.04


----Trinity----
         venue  freq
0          Bar  0.13
1   Restaurant  0.06
2  Coffee Shop  0.06
3  Men's Store  0.06
4         Café  0.04


----Underground city----
         venue  freq
0  Coffee Shop  0.12
1         Café  0.07
2          Gym  0.04
3        Hotel  0.04
4   Steakhouse  0.04


----Union Station----
                venue  freq
0         Coffee Shop  0.12
1            Aquarium  0.05
2               Hotel  0.04
3  Italian Restaurant  0.04
4                Café  0.04


----University of Toronto----
                 venue  freq
0                 Café  0.14
1               Bakery  0.06
2  Japanese Restaurant  0.06
3            Bookstore  0.06
4       Sandwich Place  0.06


----Upwood Park----
                        venue  freq
0                      Bakery  0

Returns the top venues for a given row (neighborhood)

In [89]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now we can generate a dataframe of neighborhoods and theie most common venues

In [117]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood      1st Most Common Venue 2nd Most Common Venue  \
0         Adelaide                Coffee Shop            Steakhouse   
1        Agincourt  Latin American Restaurant                Lounge   
2  Agincourt North                       Park            Playground   
3   Albion Gardens              Grocery Store          Liquor Store   
4        Alderwood                Pizza Place                   Gym   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Bar                  Café       Thai Restaurant   
1        Clothing Store          Skating Rink        Breakfast Spot   
2      Doner Restaurant      Department Store          Dessert Shop   
3              Pharmacy           Pizza Place            Beer Store   
4              Pharmacy    Athletics & Sports                   Pub   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Restaurant      Asian Restaurant                 Hotel   
1   Empanada Restaurant  Ethiopian Restaurant     Electronics Store   
2    Dim Sum Restaurant                 Diner        Discount Store   
3  Fast Food Restaurant   Fried Chicken Joint        Sandwich Place   
4        Sandwich Place          Dance Studio          Skating Rink   

  9th Most Common Venue       10th Most Common Venue  
0        Breakfast Spot               Cosmetics Shop  
1    Dim Sum Restaurant  Eastern European Restaurant  
2               Dog Run                   Donut Shop  
3         Women's Store                      Dog Run  
4           Coffee Shop          Dumpling Restaurant

Compare the neighborhoods,separating them using k-means clustering

In [118]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 0, 1, 1, 1, 1, 1, 1, 1])

and add the cluster labels to a new dataframe: toronto_merged

In [119]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = postdf

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
toronto_merged.dropna(axis=0, how='any', inplace=True)
toronto_merged # check the last columns!

Borough                                       Neighborhood  \
0          North York                                          Parkwoods   
1          North York                                   Victoria Village   
2    Downtown Toronto                                       Harbourfront   
3          North York                                   Lawrence Heights   
4          North York                                     Lawrence Manor   
5    Downtown Toronto                                       Queen's Park   
6        Queen's Park                                       Queen's Park   
7         Scarborough                                              Rouge   
8         Scarborough                                            Malvern   
9          North York                                    Don Mills North   
10          East York                                   Woodbine Gardens   
11          East York                                      Parkview Hill   
12   Downtown Toronto                                            Ryerson   
13   Downtown Toronto                                    Garden District   
14         North York                                          Glencairn   
20        Scarborough                                     Highland Creek   
21        Scarborough                                         Rouge Hill   
22        Scarborough                                         Port Union   
23         North York                                    Flemingdon Park   
24         North York                                    Don Mills South   
25          East York                                   Woodbine Heights   
26   Downtown Toronto                                     St. James Town   
27               York                                 Humewood-Cedarvale   
28          Etobicoke                                  Bloordale Gardens   
29          Etobicoke                                           Eringate   
30          Etobicoke                                      Markland Wood   
31          Etobicoke                                  Old Burnhamthorpe   
32        Scarborough                                          Guildwood   
33        Scarborough                                        Morningside   
34        Scarborough                                          West Hill   
35       East Toronto                                        The Beaches   
36   Downtown Toronto                                        Berczy Park   
37               York                                Caledonia-Fairbanks   
38        Scarborough                                             Woburn   
39          East York                                            Leaside   
40   Downtown Toronto                                 Central Bay Street   
41   Downtown Toronto                                           Christie   
42        Scarborough                                          Cedarbrae   
43         North York                                  Hillcrest Village   
44         North York                                     Bathurst Manor   
45         North York                                    Downsview North   
46         North York                                     Wilson Heights   
47          East York                                   Thorncliffe Park   
48   Downtown Toronto                                           Adelaide   
49   Downtown Toronto                                               King   
50   Downtown Toronto                                           Richmond   
51       West Toronto                                 Dovercourt Village   
52       West Toronto                                           Dufferin   
53        Scarborough                                Scarborough Village   
54         North York                                           Fairview   
55         North York                                         Henry Farm   
56         North York                                         

Create a map with color coded markers to show similar neighborhoods

In [120]:
# create map
map_clusters = folium.Map(location=[t_latitude, t_longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['lati'], toronto_merged['longi'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters


In [121]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
0               Parkwoods             0.0                  Park   
37    Caledonia-Fairbanks             0.0                  Park   
53    Scarborough Village             0.0            Playground   
59           East Toronto             0.0                  Park   
69            CFB Toronto             0.0                  Park   
70         Downsview East             0.0                  Park   
115                Weston             0.0                  Park   
119       York Mills West             0.0                  Park   
136     Kingsview Village             0.0                  Park   
137  Martin Grove Gardens             0.0                  Park   
138      Richview Gardens             0.0                  Park   
139          St. Phillips             0.0                  Park   
154       Agincourt North             0.0                  Park   
155       L'Amoreaux East             0.0                  Park   
156              Milliken             0.0                  Park   
157          Steeles East             0.0                  Park   
182              Rosedale             0.0                  Park   
192          The Kingsway             0.0                  Park   
193       Montgomery Road             0.0                  Park   
194        Old Mill North             0.0                  Park   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0       Food & Drink Shop                  Pool      Doner Restaurant   
37   Fast Food Restaurant         Women's Store           Golf Course   
53          Women's Store            Donut Shop          Dessert Shop   
59          Metro Station     Convenience Store   Empanada Restaurant   
69            Snack Place               Airport            Donut Shop   
70            Snack Place               Airport            Donut Shop   
115      Department Store           Event Space  Ethiopian Restaurant   
119                  Bank         Moving Target     Convenience Store   
136           Pizza Place        Sandwich Place     Mobile Phone Shop   
137           Pizza Place        Sandwich Place     Mobile Phone Shop   
138           Pizza Place        Sandwich Place     Mobile Phone Shop   
139           Pizza Place        Sandwich Place     Mobile Phone Shop   
154            Playground      Doner Restaurant      Department Store   
155            Playground      Doner Restaurant      Department Store   
156            Playground      Doner Restaurant      Department Store   
157            Playground      Doner Restaurant      Department Store   
182            Playground                 Trail      Doner Restaurant   
192                 River    College Rec Center         Deli / Bodega   
193                 River    College Rec Center         Deli / Bodega   
194                 River    College Rec Center         Deli / Bodega   

    5th Most Common Venue        6th Most Common Venue  \
0            Dessert Shop           Dim Sum Restaurant   
37          Deli / Bodega          Empanada Restaurant   
53     Dim Sum Restaurant                        Diner   
59      Electronics Store  Eastern European Restaurant   
69     Dim Sum Restaurant                        Diner   
70     Dim Sum Restaurant                        Diner   
115   Empanada Restaurant            Electronics Store   
119      Doner Restaurant           Dim Sum Restaurant   
136        Discount Store                Deli / Bodega   
137        Discount Store                Deli / Bodega   
138        Discount Store                Deli / Bodega   
139        Discount Store                Deli / Bodega   
154          Dessert Shop           Dim Sum Restaurant   
155          Dessert Shop           Dim Sum Restaurant   
156          Dessert Shop           Dim Sum Restaurant   
157          Dessert Shop           Dim Sum Restaurant   
182          Dessert Shop           Dim Sum Restaurant   
192   Empanada Restaurant  

In [122]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels  \
1                                     Victoria Village             1.0   
2                                         Harbourfront             1.0   
3                                     Lawrence Heights             1.0   
4                                       Lawrence Manor             1.0   
5                                         Queen's Park             1.0   
6                                         Queen's Park             1.0   
9                                      Don Mills North             1.0   
10                                    Woodbine Gardens             1.0   
11                                       Parkview Hill             1.0   
12                                             Ryerson             1.0   
13                                     Garden District             1.0   
14                                           Glencairn             1.0   
20                                      Highland Creek             1.0   
21                                          Rouge Hill             1.0   
22                                          Port Union             1.0   
23                                     Flemingdon Park             1.0   
24                                     Don Mills South             1.0   
25                                    Woodbine Heights             1.0   
26                                      St. James Town             1.0   
27                                  Humewood-Cedarvale             1.0   
28                                   Bloordale Gardens             1.0   
29                                            Eringate             1.0   
30                                       Markland Wood             1.0   
31                                   Old Burnhamthorpe             1.0   
32                                           Guildwood             1.0   
33                                         Morningside             1.0   
34                                           West Hill             1.0   
35                                         The Beaches             1.0   
36                                         Berczy Park             1.0   
38                                              Woburn             1.0   
39                                             Leaside             1.0   
40                                  Central Bay Street             1.0   
41                                            Christie             1.0   
42                                           Cedarbrae             1.0   
43                                   Hillcrest Village             1.0   
44                                      Bathurst Manor             1.0   
45                                     Downsview North             1.0   
46                                      Wilson Heights             1.0   
47                                    Thorncliffe Park             1.0   
48                                            Adelaide             1.0   
49                                                King             1.0   
50                                            Richmond             1.0   
51                                  Dovercourt Village             1.0   
52                                            Dufferin             1.0   
54                                            Fairview             1.0   
55                                          Henry Farm             1.0   
56                                              Oriole             1.0   
57                                      Northwood Park             1.0   
58                                     York University             1.0   
60                                   Harbourfront East             1.0   
61                                     Toronto Islands             1.0   
62                                       Union Station             1.0   
63                                     Little Portugal             1.0   
64                                            

In [123]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
81  Silver Hills             2.0             Cafeteria         Women's Store   
82    York Mills             2.0             Cafeteria         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
81            Donut Shop    Dim Sum Restaurant                 Diner   
82            Donut Shop    Dim Sum Restaurant                 Diner   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
81        Discount Store               Dog Run      Doner Restaurant   
82        Discount Store               Dog Run      Doner Restaurant   

   9th Most Common Venue 10th Most Common Venue  
81             Drugstore       Department Store  
82             Drugstore       Department Store

In [124]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
105                     Emery             3.0        Baseball Field   
106                 Humberlea             3.0        Baseball Field   
197                Humber Bay             3.0        Baseball Field   
198          King's Mill Park             3.0        Baseball Field   
199  Kingsway Park South East             3.0        Baseball Field   
200                 Mimico NE             3.0        Baseball Field   
201            Old Mill South             3.0        Baseball Field   
202        The Queensway East             3.0        Baseball Field   
203     Royal York South East             3.0        Baseball Field   
204                  Sunnylea             3.0        Baseball Field   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
105         Women's Store          Dessert Shop           Event Space   
106         Women's Store          Dessert Shop           Event Space   
197         Women's Store          Dessert Shop           Event Space   
198         Women's Store          Dessert Shop           Event Space   
199         Women's Store          Dessert Shop           Event Space   
200         Women's Store          Dessert Shop           Event Space   
201         Women's Store          Dessert Shop           Event Space   
202         Women's Store          Dessert Shop           Event Space   
203         Women's Store          Dessert Shop           Event Space   
204         Women's Store          Dessert Shop           Event Space   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
105  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
106  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
197  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
198  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
199  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
200  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
201  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
202  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
203  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   
204  Ethiopian Restaurant   Empanada Restaurant     Electronics Store   

           8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
105  Eastern European Restaurant   Dumpling Restaurant              Drugstore  
106  Eastern European Restaurant   Dumpling Restaurant              Drugstore  
197  Eastern European Restaurant   Dumpling Restaurant              Drugstore  
198  Eastern European Restaurant   Dumpling Restaurant              Drugstore  
199  Eastern European Restaurant   Dumpling Restaurant              Drugstore  
200  Eastern European Restaurant   Dumpling Restaurant              Drugstore  
201  Eastern European Restaurant   Dumpling Restaurant              Drugstore  
202  Eastern European Restaurant   Dumpling Restaurant              Drugstore  
203  Eastern European Restaurant   Dumpling Restaurant              Drugstore  
204  Eastern European Restaurant   Dumpling Restaurant              Drugstore

In [125]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
7        Rouge             4.0  Fast Food Restaurant      Department Store   
8      Malvern             4.0  Fast Food Restaurant      Department Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
7           Event Space  Ethiopian Restaurant   Empanada Restaurant   
8           Event Space  Ethiopian Restaurant   Empanada Restaurant   

  6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
7     Electronics Store  Eastern European Restaurant   Dumpling Restaurant   
8     Electronics Store  Eastern European Restaurant   Dumpling Restaurant   

  9th Most Common Venue 10th Most Common Venue  
7             Drugstore             Donut Shop  
8             Drugstore             Donut Shop

Summary: 
There are generally five types ofneighborhoods described in Totonto:
Cluster 0: Parks and playgrounds are quite common
Cluster 1: Liquor and beer stores dominate
Cluster 2: Cafeterias and women's stores
Cluster 3: Near baseball
Cluster 4: Fast food and department stores